In [1]:
import logging
from pathlib import Path
import os
import sys
import mne
import torch
import numpy as np
import bm
from bm import play
from bm.train import main
from bm.events import Word
from matplotlib import pyplot as plt
from IPython import display as disp

mne.set_log_level(False)
logging.basicConfig(stream=sys.stdout, level=logging.INFO)
os.chdir(main.dora.dir.parent)
os.environ['NO_DOWNLOAD'] = '1'
from tqdm import tqdm
import IPython.display as ipd
from torch.nn.functional import conv2d, conv1d
import torch.nn.functional as F
import pandas as pd

Hostname bagration not defined in /conf/study_paths/study_paths.yaml. Using default paths.


In [2]:
sig='e6d65444'

In [3]:
solver = play.get_solver_from_sig(sig) 

INFO:bm.play:Loading solver from XP e6d65444. Overrides used: ['model=clip_conv', 'dset.selections=["gwilliams2022"]', 'dset.bandpass=true', 'dset.bandpass_high=0.1', 'dset.bandpass_lower=40.0', 'seed=2038', 'clip.probabilities=true']
{'wandb': {'use_wandb': True, 'project': 'brainmagick', 'group': 'brainmagick-group'}, 'num_prints': 5, 'device': 'cuda:1', 'num_workers': 5, 'verbose': 0, 'show': 0, 'download_only': False, 'slurm': {'mem_per_gpu': 100, 'time': 4320}, 'continue_sig': None, 'continue_best': True, 'seed': 2038, 'dummy': None, 'cache': '/home/zubrikhina/brainmagick_MICCAI/cache', 'features_models': './features_models', 'early_stop_patience': 10, 'eval_every': 1, 'eval_train_set': False, 'optim': {'name': 'adam', 'shuffle': False, 'lr': 0.0003, 'beta2': 0.999, 'epochs': 200, 'batch_size': 256, 'loss': 'clip', 'weight_decay': 0.0, 'use_weighting': False, 'max_batches': 1200, 'svd': 0.0, 'negatives': None, 'negative_pool_size': None}, 'clip': {'linear': None, 'twin': True, 'po

/home/zubrikhina/brainmagick_MICCAI/bm/studies/gwilliams2022.py:105: RuntimeWarning: The unit for channel(s) MISC 001, MISC 002, MISC 003, MISC 004, MISC 005, MISC 006, MISC 007, MISC 008, MISC 009, MISC 010, MISC 011, MISC 012, MISC 013, MISC 014, MISC 015, MISC 016, MISC 017, MISC 018, MISC 019, MISC 020, MISC 021, MISC 022, MISC 023, MISC 024, MISC 025, MISC 026, MISC 027, MISC 028, MISC 029, MISC 030, MISC 031, MISC 032 has changed from V to NA.
  raw = read_raw_bids(bids_path)  # FIXME this is NOT a lazy read
/home/zubrikhina/brainmagick_MICCAI/bm/studies/gwilliams2022.py:105: RuntimeWarning: The unit for channel(s) MISC 001, MISC 002, MISC 003, MISC 004, MISC 005, MISC 006, MISC 007, MISC 008, MISC 009, MISC 010, MISC 011, MISC 012, MISC 013, MISC 014, MISC 015, MISC 016, MISC 017, MISC 018, MISC 019, MISC 020, MISC 021, MISC 022, MISC 023, MISC 024, MISC 025, MISC 026, MISC 027, MISC 028, MISC 029, MISC 030, MISC 031, MISC 032 has changed from V to NA.
  raw = read_raw_bids(bids

IndexError: index 0 is out of bounds for axis 0 with size 0

In [4]:
## SegmentDataset

In [5]:
segment =solver.datasets.train.datasets[0]

In [6]:
segment.events.columns

Index(['story', 'story_uid', 'sound_id', 'kind', 'start', 'sound', 'duration',
       'filepath', 'phoneme', 'sequence_id', 'condition', 'word_index',
       'speech_rate', 'voice', 'pronounced', 'word', 'language', 'modality',
       'word_sequence', 'phoneme_id', 'offset', 'uid'],
      dtype='object')

In [7]:
segment.events.loc[segment.events.kind =='sound'][["start", "offset"]]

start  offset
0      23.506    0.00
97     29.756    6.25
259    40.096   16.59
497    68.416   44.91
584    79.166   55.66
661    91.926   68.42
723    98.206   74.70
817   109.876   86.37
889   127.185    0.00
925   131.415    4.23
1074  145.945   18.76
1160  155.075   27.89
1266  164.915   37.73
1355  173.305   46.12
1468  187.115   59.93
1559  210.048    0.00
1673  220.108   10.06
1751  227.718   17.67
1806  234.828   24.78
1935  248.578   38.53
2020  256.248   46.20
2132  265.918   55.87
2236  275.888   65.84
2300  282.218   72.17
2474  296.228   86.18
2605  311.027    0.00
2735  320.967    9.94
2922  333.877   22.85
3111  357.677   46.65

In [8]:
segment.events.columns

Index(['story', 'story_uid', 'sound_id', 'kind', 'start', 'sound', 'duration',
       'filepath', 'phoneme', 'sequence_id', 'condition', 'word_index',
       'speech_rate', 'voice', 'pronounced', 'word', 'language', 'modality',
       'word_sequence', 'phoneme_id', 'offset', 'uid'],
      dtype='object')

In [9]:
segment._get_bounds_times(0)

(30.25, 34.25833333333333)

In [10]:
feature_data, feature_mask, events = segment._get_feature(0)

In [11]:
events

[DataSlice(start=30.25, duration=4.008333333333333, modality=None, language=None, sample_rate=120.0),
 Sound(start=29.756, duration=10.339999999999996, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/lw1_0.wav', offset=6.25),
 Word(start=29.896, duration=0.3900000000000005, modality='audio', language='english', word='gentle', word_index=1, word_sequence='The gentle constant breeze of recycled air from the vent above blew an annoying hair against her nose but she ignored it'),
 Word(start=30.286, duration=0.4199999999999999, modality='audio', language='english', word='constant', word_index=2, word_sequence='The gentle constant breeze of recycled air from the vent above blew an annoying hair against her nose but she ignored it'),
 Word(start=30.706, duration=0.2099999999999999, modality='audio', language='english', word='breeze', word_index=3, word_sequence='The gentle constant breeze of recycled air from the v

In [12]:
feature_data

tensor([[ 1.9195,  1.9195,  1.9195,  ..., -0.2759, -2.3508, -2.3508],
        [ 2.6633,  2.6633,  2.6633,  ..., -0.0616, -2.7648, -2.7648],
        [ 3.5532,  3.5532,  3.5532,  ...,  0.0917,  3.3258,  3.3258],
        ...,
        [-4.5396, -4.5396, -4.5396,  ...,  2.0538,  0.7065,  0.7065],
        [ 2.6481,  2.6481,  2.6481,  ...,  0.3304,  1.4277,  1.4277],
        [-3.8462, -3.8462, -3.8462,  ...,  4.6554,  2.9859,  2.9859]])

In [13]:
feature_data1, feature_mask1, events1 = segment._get_feature(1)

In [14]:
events1

[DataSlice(start=30.75, duration=4.008333333333333, modality=None, language=None, sample_rate=120.0),
 Sound(start=29.756, duration=10.339999999999996, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/lw1_0.wav', offset=6.25),
 Word(start=30.706, duration=0.2099999999999999, modality='audio', language='english', word='breeze', word_index=3, word_sequence='The gentle constant breeze of recycled air from the vent above blew an annoying hair against her nose but she ignored it'),
 Word(start=30.916, duration=0.1200000000000001, modality='audio', language='english', word='of', word_index=4, word_sequence='The gentle constant breeze of recycled air from the vent above blew an annoying hair against her nose but she ignored it'),
 Word(start=31.036, duration=0.4100000000000001, modality='audio', language='english', word='recycled', word_index=5, word_sequence='The gentle constant breeze of recycled air from the vent 

In [15]:
feature_data[0, 61:]

tensor([ 2.6716,  2.6716,  3.5960,  3.5960,  3.3536,  3.3536,  3.3536,  4.2903,
         4.2903,  3.9825,  3.9825,  3.9825,  3.6847,  3.6847,  0.1760,  0.1760,
         3.6288,  3.6288,  3.6288,  2.9609,  2.9609,  0.7686,  0.7686,  0.7686,
         1.8156,  1.8156,  3.8117,  3.8117, -7.2355, -7.2355, -7.2355, -0.0898,
        -0.0898, -0.5162, -0.5162, -0.5162,  3.0891,  3.0891,  3.6898,  3.6898,
         3.6898,  4.1622,  4.1622,  1.6759,  1.6759, -1.1674, -1.1674, -1.1674,
        -1.9852, -1.9852,  2.2801,  2.2801,  2.2801,  4.5035,  4.5035,  7.2958,
         7.2958,  2.1513,  2.1513,  2.1513,  1.1973,  1.1973,  0.5745,  0.5745,
         0.5745,  2.7003,  2.7003,  1.8794,  1.8794,  0.4258,  0.4258,  0.4258,
        -0.3375, -0.3375,  3.5061,  3.5061,  3.5061,  6.1423,  6.1423,  4.1697,
         4.1697,  5.4751,  5.4751,  5.4751,  3.0835,  3.0835, -0.2030, -0.2030,
        -0.2030,  1.8715,  1.8715,  1.0674,  1.0674,  0.7691,  0.7691,  0.7691,
         1.1238,  1.1238,  3.1219,  3.12

In [16]:
feature_data1[0, :-61]

tensor([ 2.6716,  2.6716,  2.6716,  3.5960,  3.5960,  3.3536,  3.3536,  3.3536,
         4.2903,  4.2903,  3.9825,  3.9825,  3.9825,  3.6847,  3.6847,  0.1760,
         0.1760,  3.6288,  3.6288,  3.6288,  2.9609,  2.9609,  0.7686,  0.7686,
         0.7686,  1.8156,  1.8156,  3.8117,  3.8117, -7.2355, -7.2355, -7.2355,
        -0.0898, -0.0898, -0.5162, -0.5162, -0.5162,  3.0891,  3.0891,  3.6898,
         3.6898,  4.1622,  4.1622,  4.1622,  1.6759,  1.6759, -1.1674, -1.1674,
        -1.1674, -1.9852, -1.9852,  2.2801,  2.2801,  4.5035,  4.5035,  4.5035,
         7.2958,  7.2958,  2.1513,  2.1513,  2.1513,  1.1973,  1.1973,  0.5745,
         0.5745,  2.7003,  2.7003,  2.7003,  1.8794,  1.8794,  0.4258,  0.4258,
         0.4258, -0.3375, -0.3375,  3.5061,  3.5061,  6.1423,  6.1423,  6.1423,
         4.1697,  4.1697,  5.4751,  5.4751,  5.4751,  3.0835,  3.0835, -0.2030,
        -0.2030,  1.8715,  1.8715,  1.8715,  1.0674,  1.0674,  0.7691,  0.7691,
         0.7691,  1.1238,  1.1238,  3.12

In [17]:
feature_data1[0, :] @ feature_data[0, :]

tensor(1407.8538)

In [18]:
feature_data[0, :] @ feature_data[0, :]

tensor(4947.8921)

In [19]:
from bm.features.audio import _extract_wav_part

In [20]:
wav, sr =_extract_wav_part('/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/lw1_0.wav', 30.25, 34.25833333333333)

In [21]:
sr

22050.0

In [22]:
wav.numpy()

array([[-0.335083  , -0.32199097, -0.29586792, ...,  0.10470581,
         0.16851807,  0.19934082]], dtype=float32)

In [23]:
ipd.Audio(data=wav.numpy(), autoplay=True, rate=sr)

In [24]:
wav2, sr =_extract_wav_part('/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/lw1_0.wav', 6.25, 10.339999999999996+6.25)

In [25]:
ipd.Audio(data=wav2.numpy(), autoplay=True, rate=sr)

In [26]:
def _get_one_segments_and_vocabs(solver):
    from scripts.run_eval_probs import _get_extra_info
    split ='train'
    segments,vocab, estimates,outputs,features_masks, reject_masks = [], [],[], [],[], []
    dset = getattr(solver.datasets, split)
    loader = solver.make_loader(dset, shuffle=False)
    test_features = solver.datasets.test.datasets[0].features
    for idx, batch in tqdm(enumerate(loader)):
        #features = test_features.extract_features(batch.features, solver.used_features.keys())
        with torch.no_grad():
            estimate, output, features_mask, reject_mask = solver._process_batch(batch)
            data,  words, word_segs= _get_extra_info(batch, solver.args.dset.sample_rate)
        if idx>1:
            break
    return batch, estimate, output, word_segs,vocab

In [27]:
batch, estimate, output, word_segs,vocab = _get_one_segments_and_vocabs(solver)

2it [00:11,  5.81s/it]


In [47]:
batch

SegmentBatch(meg=tensor([[[ 2.0759e-13,  6.3198e-14,  6.3428e-14,  ...,  2.2503e-13,
           1.6551e-13,  1.3378e-13],
         [ 7.6279e-14, -2.8972e-14, -5.0357e-14,  ..., -4.6946e-13,
          -6.0660e-13, -7.7874e-13],
         [ 1.4206e-13,  1.3440e-13,  7.2975e-15,  ...,  3.4285e-13,
           2.5804e-13,  2.0576e-14],
         ...,
         [ 4.3529e-13,  2.3561e-13,  5.7475e-14,  ...,  5.0128e-13,
           6.4223e-13,  6.3869e-13],
         [-3.7385e-14, -2.1035e-13, -2.1831e-13,  ...,  6.5488e-13,
           6.0711e-13,  5.8224e-13],
         [ 1.9217e-13,  4.4493e-14, -7.2709e-14,  ..., -1.8081e-14,
           3.0878e-14,  3.8994e-14]],

        [[-5.5693e-14, -6.0496e-14, -4.0227e-15,  ...,  1.9134e-13,
           3.3339e-13,  3.1649e-13],
         [ 5.0039e-14,  8.0237e-14,  1.1545e-13,  ..., -4.6999e-13,
          -2.9308e-13, -2.5279e-13],
         [-2.5166e-13, -2.3434e-13, -6.1609e-14,  ..., -1.7750e-13,
          -1.0242e-13,  1.1481e-13],
         ...,
        

In [28]:
word_segs[0]

'of his eye Two forts stood on the playground and a hot'

In [29]:
batch._event_lists[0]

[DataSlice(start=96.25, duration=4.00833333333334, modality=None, language=None, sample_rate=120.0),
 Sound(start=94.165, duration=8.849999999999994, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', offset=85.92),
 Word(start=96.185, duration=0.1299999999999954, modality='audio', language='english', word='of', word_index=9, word_sequence='Chad checked the other fort out of the corner of his eye'),
 Word(start=96.315, duration=0.1400000000000005, modality='audio', language='english', word='his', word_index=10, word_sequence='Chad checked the other fort out of the corner of his eye'),
 Word(start=96.455, duration=0.0900000000000034, modality='audio', language='english', word='eye', word_index=11, word_sequence='Chad checked the other fort out of the corner of his eye'),
 Word(start=97.735, duration=0.2100000000000079, modality='audio', language='english', word='Two', word_index=0, word_s

In [30]:
wav3, sr =_extract_wav_part('/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', 85.92, 8.849999999999994+85.92)

In [31]:
ipd.Audio(data=wav3.numpy(), autoplay=True, rate=sr)

In [49]:
events_all =pd.read_csv('cache/studies/gwilliams2022/01_session0_story1/events.csv')

In [32]:
word_segs

array(['of his eye Two forts stood on the playground and a hot',
       'Two forts stood on the playground and a hot bare battlefield',
       'Two forts stood on the playground and a hot bare battlefield',
       'Two forts stood on the playground and a hot bare battlefield separated',
       'stood on the playground and a hot bare battlefield separated them',
       'playground and a hot bare battlefield separated them',
       'massive rusted A frame swing marked the border though nobody was swinging',
       'rusted A frame swing marked the border though nobody was swinging in the hot',
       'rusted A frame swing marked the border though nobody was swinging in the hot sun',
       'frame swing marked the border though nobody was swinging in the hot sun',
       'swing marked the border though nobody was swinging in the hot sun',
       'the border though nobody was swinging in the hot sun',
       'though nobody was swinging in the hot sun',
       'was swinging in the hot sun', 

In [69]:
np.where(word_segs == "")

(array([ 16,  17,  18,  19,  20,  21, 138, 139, 140, 141, 142, 143, 144,
        145, 188, 189, 190, 191, 192, 201, 202, 203, 204, 205, 206, 207,
        217, 218, 219, 220, 230]),)

In [72]:
batch._event_lists[15]

[DataSlice(start=107.75, duration=4.00833333333334, modality=None, language=None, sample_rate=120.0),
 Sound(start=103.015, duration=5.827777777777783, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', offset=94.77),
 Word(start=107.515, duration=0.2400000000000091, modality='audio', language='english', word='hot', word_index=15, word_sequence='A massive rusted A frame swing marked the border though nobody was swinging in the hot sun'),
 Word(start=107.765, duration=0.3200000000000074, modality='audio', language='english', word='sun', word_index=16, word_sequence='A massive rusted A frame swing marked the border though nobody was swinging in the hot sun')]

In [70]:
batch._event_lists[16]

[DataSlice(start=108.25, duration=4.00833333333334, modality=None, language=None, sample_rate=120.0),
 Sound(start=103.015, duration=5.827777777777783, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', offset=94.77)]

In [80]:
103.015+5.827777777777783

108.84277777777778

In [81]:
batch._event_lists[17]

[DataSlice(start=108.75, duration=4.00833333333334, modality=None, language=None, sample_rate=120.0),
 Sound(start=103.015, duration=5.827777777777783, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', offset=94.77)]

In [73]:
events_all.loc[events_all.word_sequence=='A massive rusted A frame swing marked the border though nobody was swinging in the hot sun']

story  story_uid  sound_id  kind    start  \
1222  cable_spool_fort        1.0       0.0  word  103.015   
1224  cable_spool_fort        1.0       0.0  word  103.115   
1230  cable_spool_fort        1.0       0.0  word  103.825   
1236  cable_spool_fort        1.0       0.0  word  104.275   
1239  cable_spool_fort        1.0       0.0  word  104.775   
1244  cable_spool_fort        1.0       0.0  word  105.155   
1248  cable_spool_fort        1.0       0.0  word  105.485   
1255  cable_spool_fort        1.0       0.0  word  105.755   
1258  cable_spool_fort        1.0       0.0  word  105.855   
1263  cable_spool_fort        1.0       0.0  word  106.175   
1267  cable_spool_fort        1.0       0.0  word  106.305   
1274  cable_spool_fort        1.0       0.0  word  106.725   
1277  cable_spool_fort        1.0       0.0  word  106.905   
1284  cable_spool_fort        1.0       0.0  word  107.335   
1287  cable_spool_fort        1.0       0.0  word  107.425   
1290  cable_spool_fort        1.0       0.0  word  107.515   
1295  cable_spool_fort        1.0       0.0  word  107.765   

                                     sound  duration filepath phoneme  \
1222  stimuli/audio/cable_spool_fort_0.wav      0.10      NaN     NaN   
1224  stimuli/audio/cable_spool_fort_0.wav      0.53      NaN     NaN   
1230  stimuli/audio/cable_spool_fort_0.wav      0.45      NaN     NaN   
1236  stimuli/audio/cable_spool_fort_0.wav      0.29      NaN     NaN   
1239  stimuli/audio/cable_spool_fort_0.wav      0.38      NaN     NaN   
1244  stimuli/audio/cable_spool_fort_0.wav      0.33      NaN     NaN   
1248  stimuli/audio/cable_spool_fort_0.wav      0.26      NaN     NaN   
1255  stimuli/audio/cable_spool_fort_0.wav      0.10      NaN     NaN   
1258  stimuli/audio/cable_spool_fort_0.wav      0.32      NaN     NaN   
1263  stimuli/audio/cable_spool_fort_0.wav      0.13      NaN     NaN   
1267  stimuli/audio/cable_spool_fort_0.wav      0.42      NaN     NaN   
1274  stimuli/audio/cable_spool_fort_0.wav      0.18      NaN     NaN   
1277  stimuli/audio/cable_spool_fort_0.wav      0.43      NaN     NaN   
1284  stimuli/audio/cable_spool_fort_0.wav      0.09      NaN     NaN   
1287  stimuli/audio/cable_spool_fort_0.wav      0.08      NaN     NaN   
1290  stimuli/audio/cable_spool_fort_0.wav      0.24      NaN     NaN   
1295  stimuli/audio/cable_spool_fort_0.wav      0.32      NaN     NaN   

      sequence_id  ... speech_rate    voice  pronounced      word  language  \
1222         21.0  ...       175.0  Allison         1.0         A   english   
1224         21.0  ...       175.0  Allison         1.0   massive   english   
1230         21.0  ...       175.0  Allison         1.0    rusted   english   
1236         21.0  ...       175.0  Allison         1.0         A   english   
1239         21.0  ...       175.0  Allison         1.0     frame   english   
1244         21.0  ...       175.0  Allison         1.0     swing   english   
1248         21.0  ...       175.0  Allison         1.0    marked   english   
1255         21.0  ...       175.0  Allison         1.0       the   english   
1258         21.0  ...       175.0  Allison         1.0    border   english   
1263         21.0  ...       175.0  Allison         1.0    though   english   
1267         21.0  ...       175.0  Allison         1.0    nobody   english   
1274         21.0  ...       175.0  Allison         1.0       was   english   
1277         21.0  ...       175.0  Allison         1.0  swinging   english   
1284         21.0  ...       175.0  Allison         1.0        in   english   
1287         21.0  ...       175.0  Allison         1.0       the   english   
1290         21.0  ...       175.0  Allison         1.0       hot   english   
1295         21.0  ...       175.0  Allison         1.0       sun   english   

     modality                                      word_sequence phoneme_id  \
1222    audio  A massive rusted A frame swing marked the bord...        NaN   
1224

In [83]:
events_all.iloc[1218:1270, :]

story  story_uid  sound_id     kind    start  \
1218  cable_spool_fort        1.0       0.0  phoneme  101.925   
1219  cable_spool_fort        1.0       0.0  phoneme  101.995   
1220               NaN        NaN       NaN    block  103.015   
1221  cable_spool_fort        1.0       0.0  phoneme  103.015   
1222  cable_spool_fort        1.0       0.0     word  103.015   
1223  cable_spool_fort        1.0       0.0  phoneme  103.115   
1224  cable_spool_fort        1.0       0.0     word  103.115   
1225  cable_spool_fort        1.0       0.0  phoneme  103.215   
1226  cable_spool_fort        1.0       0.0  phoneme  103.345   
1227  cable_spool_fort        1.0       0.0  phoneme  103.425   
1228  cable_spool_fort        1.0       0.0  phoneme  103.535   
1229  cable_spool_fort        1.0       0.0  phoneme  103.825   
1230  cable_spool_fort        1.0       0.0     word  103.825   
1231  cable_spool_fort        1.0       0.0  phoneme  103.965   
1232  cable_spool_fort        1.0       0.0  phoneme  104.025   
1233  cable_spool_fort        1.0       0.0  phoneme  104.075   
1234  cable_spool_fort        1.0       0.0  phoneme  104.135   
1235  cable_spool_fort        1.0       0.0  phoneme  104.175   
1236  cable_spool_fort        1.0       0.0     word  104.275   
1237  cable_spool_fort        1.0       0.0  phoneme  104.275   
1238  cable_spool_fort        1.0       0.0  phoneme  104.775   
1239  cable_spool_fort        1.0       0.0     word  104.775   
1240  cable_spool_fort        1.0       0.0  phoneme  104.875   
1241  cable_spool_fort        1.0       0.0  phoneme  104.955   
1242  cable_spool_fort        1.0       0.0  phoneme  105.085   
1243  cable_spool_fort        1.0       0.0  phoneme  105.155   
1244  cable_spool_fort        1.0       0.0     word  105.155   
1245  cable_spool_fort        1.0       0.0  phoneme  105.235   
1246  cable_spool_fort        1.0       0.0  phoneme  105.285   
1247  cable_spool_fort        1.0       0.0  phoneme  105.385   
1248  cable_spool_fort        1.0       0.0     word  105.485   
1249  cable_spool_fort        1.0       0.0  phoneme  105.485   
1250  cable_spool_fort        1.0       0.0  phoneme  105.535   
1251  cable_spool_fort        1.0       0.0  phoneme  105.635   
1252  cable_spool_fort        1.0       0.0  phoneme  105.675   
1253  cable_spool_fort        1.0       0.0  phoneme  105.735   
1254  cable_spool_fort        1.0       0.0  phoneme  105.755   
1255  cable_spool_fort        1.0       0.0     word  105.755   
1256  cable_spool_fort        1.0       0.0  phoneme  105.815   
1257  cable_spool_fort        1.0       0.0  phoneme  105.855   
1258  cable_spool_fort        1.0       0.0     word  105.855   
1259  cable_spool_fort        1.0       0.0  phoneme  105.925   
1260  cable_spool_fort        1.0       0.0  phoneme  106.015   
1261  cable_spool_fort        1.0       0.0  phoneme  106.045   
1262  cable_spool_fort        1.0       0.0  phoneme  106.115   
1263  cable_spool_fort        1.0       0.0     word  106.175   
1264  cable_spool_fort        1.0       0.0  phoneme  106.175   
1265  cable_spool_fort        1.0       0.0  phoneme  106.215   
1266  cable_spool_fort        1.0       0.0  phoneme  106.305   
1267  cable_spool_fort        1.0       0.0     word  106.305   
1268  cable_spool_fort        1.0       0.0  phoneme  106.405   
1269  cable_spool_fort        1.0       0.0  phoneme  106.495   

                                     sound  duration filepath phoneme  \
1218  stimuli/audio/cable_spool_fort_0.wav     0.070      NaN    ah_I   
1219  stimuli/audio/cable_spool_fort_0.wav     0.170      NaN     m_E   
1220                                   NaN    11.942      NaN     NaN   
1221  stimuli/audio/cable_spool_fort_0.wav     0.100      NaN    ah_S   
1222  stimuli/audio/cable_spool_fort_0.wav     0.100      NaN     NaN   
1223  stimuli/audio/cable_spool_fort_0.wav     0.100      NaN     m_B   
1224  stimuli/audio/cable_spool_fort_0.wav     0.530      Na

In [79]:
events_all.iloc[1270:1320, :]

story  story_uid  sound_id     kind    start  \
1270  cable_spool_fort        1.0       0.0  phoneme  106.565   
1271  cable_spool_fort        1.0       0.0  phoneme  106.605   
1272  cable_spool_fort        1.0       0.0  phoneme  106.645   
1273  cable_spool_fort        1.0       0.0  phoneme  106.725   
1274  cable_spool_fort        1.0       0.0     word  106.725   
1275  cable_spool_fort        1.0       0.0  phoneme  106.755   
1276  cable_spool_fort        1.0       0.0  phoneme  106.845   
1277  cable_spool_fort        1.0       0.0     word  106.905   
1278  cable_spool_fort        1.0       0.0  phoneme  106.905   
1279  cable_spool_fort        1.0       0.0  phoneme  107.015   
1280  cable_spool_fort        1.0       0.0  phoneme  107.065   
1281  cable_spool_fort        1.0       0.0  phoneme  107.155   
1282  cable_spool_fort        1.0       0.0  phoneme  107.205   
1283  cable_spool_fort        1.0       0.0  phoneme  107.275   
1284  cable_spool_fort        1.0       0.0     word  107.335   
1285  cable_spool_fort        1.0       0.0  phoneme  107.335   
1286  cable_spool_fort        1.0       0.0  phoneme  107.385   
1287  cable_spool_fort        1.0       0.0     word  107.425   
1288  cable_spool_fort        1.0       0.0  phoneme  107.425   
1289  cable_spool_fort        1.0       0.0  phoneme  107.475   
1290  cable_spool_fort        1.0       0.0     word  107.515   
1291  cable_spool_fort        1.0       0.0  phoneme  107.515   
1292  cable_spool_fort        1.0       0.0  phoneme  107.605   
1293  cable_spool_fort        1.0       0.0  phoneme  107.685   
1294  cable_spool_fort        1.0       0.0  phoneme  107.765   
1295  cable_spool_fort        1.0       0.0     word  107.765   
1296  cable_spool_fort        1.0       0.0  phoneme  107.835   
1297  cable_spool_fort        1.0       0.0  phoneme  107.925   
1298               NaN        NaN       NaN    block  114.957   
1299  cable_spool_fort        1.0       1.0    sound  114.957   
1300  cable_spool_fort        1.0       1.0  phoneme  114.957   
1301  cable_spool_fort        1.0       1.0     word  114.957   
1302  cable_spool_fort        1.0       1.0  phoneme  115.017   
1303  cable_spool_fort        1.0       1.0  phoneme  115.077   
1304  cable_spool_fort        1.0       1.0     word  115.077   
1305  cable_spool_fort        1.0       1.0  phoneme  115.127   
1306  cable_spool_fort        1.0       1.0  phoneme  115.237   
1307  cable_spool_fort        1.0       1.0  phoneme  115.297   
1308  cable_spool_fort        1.0       1.0  phoneme  115.407   
1309  cable_spool_fort        1.0       1.0  phoneme  115.467   
1310  cable_spool_fort        1.0       1.0     word  115.467   
1311  cable_spool_fort        1.0       1.0  phoneme  115.517   
1312  cable_spool_fort        1.0       1.0  phoneme  115.607   
1313  cable_spool_fort        1.0       1.0     word  115.607   
1314  cable_spool_fort        1.0       1.0  phoneme  115.617   
1315  cable_spool_fort        1.0       1.0  phoneme  115.677   
1316  cable_spool_fort        1.0       1.0     word  115.677   
1317  cable_spool_fort        1.0       1.0  phoneme  115.767   
1318  cable_spool_fort        1.0       1.0  phoneme  115.877   
1319  cable_spool_fort        1.0       1.0     word  115.877   

                                       sound    duration  \
1270    stimuli/audio/cable_spool_fort_0.wav    0.040000   
1271    stimuli/audio/cable_spool_fort_0.wav    0.040000   
1272    stimuli/audio/cable_spool_fort_0.wav    0.080000   
1273    stimuli/audio/cable_spool_fort_0.wav    0.030000   
1274    stimuli/audio/cable_spool_fort_0.wav    0.180000   
1275    stimuli/audio/cable_spool_fort_0.wav    0.090000   
1276    stimuli/audio/cable_spool_fort_0.wav    0.060000   
1277    stimuli/audio/cable_spool_fort_0.wav    0.430000   
1278    stimuli/audio/cable_spool_fort_0.wav    0.110000   
1279    stimuli/audio/cable_spool_fort_0.wav    0.050000   
1280    stimuli/audio/cable_spool_fort_0.

In [63]:
events_slice =events_all.loc[events_all.kind!="phoneme"].reset_index()

In [64]:
events_slice.loc[events_slice.word_sequence=='Pop said The doctors have put something very special in Roy']

index             story  story_uid  sound_id  kind    start  \
793   3282  cable_spool_fort        1.0       2.0  word  302.347   
794   3286  cable_spool_fort        1.0       2.0  word  302.687   
795   3290  cable_spool_fort        1.0       2.0  word  303.367   
796   3293  cable_spool_fort        1.0       2.0  word  303.547   
797   3299  cable_spool_fort        1.0       2.0  word  304.137   
798   3304  cable_spool_fort        1.0       2.0  word  304.457   
799   3308  cable_spool_fort        1.0       2.0  word  304.697   
800   3314  cable_spool_fort        1.0       2.0  word  305.217   
801   3320  cable_spool_fort        1.0       2.0  word  305.617   
802   3326  cable_spool_fort        1.0       2.0  word  306.127   
803   3330  cable_spool_fort        1.0       2.0  word  312.777   

                                    sound  duration filepath phoneme  ...  \
793  stimuli/audio/cable_spool_fort_2.wav      0.34      NaN     NaN  ...   
794  stimuli/audio/cable_spool_fort_2.wav      0.46      NaN     NaN  ...   
795  stimuli/audio/cable_spool_fort_2.wav      0.18      NaN     NaN  ...   
796  stimuli/audio/cable_spool_fort_2.wav      0.58      NaN     NaN  ...   
797  stimuli/audio/cable_spool_fort_2.wav      0.29      NaN     NaN  ...   
798  stimuli/audio/cable_spool_fort_2.wav      0.24      NaN     NaN  ...   
799  stimuli/audio/cable_spool_fort_2.wav      0.51      NaN     NaN  ...   
800  stimuli/audio/cable_spool_fort_2.wav      0.40      NaN     NaN  ...   
801  stimuli/audio/cable_spool_fort_2.wav      0.51      NaN     NaN  ...   
802  stimuli/audio/cable_spool_fort_2.wav      0.17      NaN     NaN  ...   
803  stimuli/audio/cable_spool_fort_2.wav      0.40      NaN     NaN  ...   

     speech_rate    voice  pronounced       word language  modality  \
793        145.0  Allison         1.0        Pop  english     audio   
794        145.0  Allison         1.0       said  english     audio   
795        145.0  Allison         1.0        The  english     audio   
796        145.0  Allison         1.0    doctors  english     audio   
797        145.0  Allison         1.0       have  english     audio   
798        145.0  Allison         1.0        put  english     audio   
799        145.0  Allison         1.0  something  english     audio   
800        145.0  Allison         1.0       very  english     audio   
801        145.0  Allison         1.0    special  english     audio   
802        145.0  Allison         1.0         in  english     audio   
803        145.0  Allison         1.0        Roy  english     audio   

                                         word_sequence phoneme_id offset  uid  
793  Pop said The doctors have put something very s...        NaN    NaN  NaN  
794  Pop said The doctors have put something very s...        NaN    NaN  NaN  
795  Pop said The doctors have put something very s...        NaN    NaN  NaN  
796  Pop said The doctors have put something very s...        NaN    NaN  NaN  
797  Pop said The doctors have put something very s...        NaN    NaN  NaN  
798  Pop said The doctors have put something very s...        NaN    NaN  NaN  
799  Pop said The doctors have put something very s...        NaN    NaN  NaN  
800  Pop said The doctors have put something very s...        NaN    NaN  NaN  
801  Pop said The doctors have put something very s...        NaN    NaN  NaN  
802  Pop said The doctors have put something very s...        NaN    NaN  NaN  
803  Pop said The doctors have put something very s...        NaN    NaN  NaN  

[11 rows x 23 columns]

In [66]:
events_slice.iloc[800:830, :]

index             story  story_uid  sound_id   kind    start  \
800   3314  cable_spool_fort        1.0       2.0   word  305.217   
801   3320  cable_spool_fort        1.0       2.0   word  305.617   
802   3326  cable_spool_fort        1.0       2.0   word  306.127   
803   3330  cable_spool_fort        1.0       2.0   word  312.777   
804   3333  cable_spool_fort        1.0       2.0   word  320.707   
805   3336  cable_spool_fort        1.0       2.0   word  326.957   
806   3339  cable_spool_fort        1.0       2.0   word  332.137   
807   3342  cable_spool_fort        1.0       2.0   word  332.447   
808   3346  cable_spool_fort        1.0       2.0   word  333.057   
809   3349  cable_spool_fort        1.0       2.0   word  333.677   
810   3354  cable_spool_fort        1.0       2.0   word  334.327   
811   3357  cable_spool_fort        1.0       2.0   word  334.667   
812   3362               NaN        NaN       NaN  block  336.317   
813   3363  cable_spool_fort        1.0       2.0   word  336.317   
814   3367  cable_spool_fort        1.0       2.0   word  336.717   
815   3372  cable_spool_fort        1.0       2.0   word  337.067   
816   3375  cable_spool_fort        1.0       2.0   word  337.227   
817   3379  cable_spool_fort        1.0       2.0   word  337.467   
818   3383  cable_spool_fort        1.0       2.0   word  338.077   
819   3388  cable_spool_fort        1.0       2.0   word  338.497   
820   3391  cable_spool_fort        1.0       2.0   word  338.897   
821   3398  cable_spool_fort        1.0       2.0   word  339.337   
822   3401  cable_spool_fort        1.0       2.0   word  340.057   
823   3407  cable_spool_fort        1.0       2.0   word  340.527   
824   3410  cable_spool_fort        1.0       2.0   word  341.877   
825   3419  cable_spool_fort        1.0       2.0   word  342.527   
826   3424  cable_spool_fort        1.0       2.0   word  343.277   
827   3428  cable_spool_fort        1.0       2.0   word  344.367   
828   3431  cable_spool_fort        1.0       2.0   word  344.697   
829   3434               NaN        NaN       NaN  block  345.777   

                                    sound  duration filepath phoneme  ...  \
800  stimuli/audio/cable_spool_fort_2.wav      0.40      NaN     NaN  ...   
801  stimuli/audio/cable_spool_fort_2.wav      0.51      NaN     NaN  ...   
802  stimuli/audio/cable_spool_fort_2.wav      0.17      NaN     NaN  ...   
803  stimuli/audio/cable_spool_fort_2.wav      0.40      NaN     NaN  ...   
804  stimuli/audio/cable_spool_fort_2.wav      0.55      NaN     NaN  ...   
805  stimuli/audio/cable_spool_fort_2.wav      0.47      NaN     NaN  ...   
806  stimuli/audio/cable_spool_fort_2.wav      0.31      NaN     NaN  ...   
807  stimuli/audio/cable_spool_fort_2.wav      0.41      NaN     NaN  ...   
808  stimuli/audio/cable_spool_fort_2.wav      0.42      NaN     NaN  ...   
809  stimuli/audio/cable_spool_fort_2.wav      0.35      NaN     NaN  ...   
810  stimuli/audio/cable_spool_fort_2.wav      0.34      NaN     NaN  ...   
811  stimuli/audio/cable_spool_fort_2.wav      0.64      NaN     NaN  ...   
812                                   NaN      9.46      NaN     NaN  ...   
813  stimuli/audio/cable_spool_fort_2.wav      0.20      NaN     NaN  ...   
814  stimuli/audio/cable_spool_fort_2.wav      0.35      NaN     NaN  ...   
815  stimuli/audio/cable_spool_fort_2.wav      0.16      NaN     NaN  ...   
816  stimuli/audio/cable_spool_fort_2.wav      0.23      NaN     NaN  ...   
817  stimuli/audio/cable_spool_fort_2.wav      0.23      NaN     NaN  ...   
818  stimuli/audio/cable_spool_fort_2.wav      0.42      NaN     NaN  ...   
819  stimuli/audio/cable_spool_fort_2.wav      0.36      NaN     NaN  ...   
820  stimuli/audio/cable_spool_fort_2.wav      0.43      NaN     NaN  ...   
821  stimuli/audio/cable_spool_fort_2.wav      0.16      NaN     NaN  ...   
822  stimuli/audio/cable_spool_fort_2.wav      0.34      NaN     NaN  ...   
823  stimuli/audi

In [67]:
wav4, sr =_extract_wav_part('/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_2.wav', 44.629999999999995, 33.97000000000003+44.629999999999995)

In [68]:
ipd.Audio(data=wav4.numpy(), autoplay=True, rate=sr)

In [33]:
batch.subject_index[194]

tensor(0)

In [34]:
batch.subject_index[193]

tensor(0)

In [35]:
scores = torch.einsum("bct,oct->bo", output, output)

In [36]:
scores[193,:].sort()

torch.return_types.sort(
values=tensor([ -1040.4744,  -1040.4744,  -1040.4744,  -1040.4744,  -1040.4744,
         -1040.4744,  -1040.4744,  -1040.4744,  -1040.4744,  -1040.4744,
         -1040.4744,   1350.7147,   1561.6619,  12609.6328,  16526.9629,
         28826.8555,  30469.7617,  40457.1289,  45959.9258,  59124.7500,
         60368.9180,  65118.1836,  65172.9570,  69158.4375,  71125.6016,
         76552.3594,  80116.0234,  83802.4766,  83947.8984,  84267.6484,
         84426.8047,  86211.3438,  86597.4219,  87915.7500,  87964.5000,
         92221.4766,  92631.1953,  95835.1016,  95939.9219,  95954.3984,
         98119.2500,  98282.3750,  99386.4062,  99896.7734,  99965.7812,
        100004.1328, 100412.0703, 101469.5312, 101528.2891, 101708.5859,
        101717.2578, 101835.3047, 102027.8438, 102572.5938, 102902.0781,
        103422.2266, 103966.6406, 104395.5391, 104421.0312, 105096.6484,
        105100.4219, 105231.1953, 105530.3359, 105791.7266, 105837.0703,
        106018.4219

In [37]:
scores_f = torch.einsum("bct,oct->bo", batch.features, batch.features)

In [38]:
scores_f[193,:].sort()

torch.return_types.sort(
values=tensor([       0.0000,        0.0000,        0.0000,        0.0000,
               0.0000,        0.0000,        0.0000,        0.0000,
               0.0000,        0.0000,        0.0000,    80851.1016,
           88165.3594,   476109.1875,   608505.1875,  1045624.2500,
         1112549.2500,  1472742.8750,  1667045.0000,  2186037.5000,
         2320733.5000,  2489101.5000,  2692286.2500,  2787718.2500,
         2972300.7500,  3008604.2500,  3025721.7500,  3185151.5000,
         3281116.5000,  3300858.2500,  3322161.0000,  3362557.7500,
         3393898.2500,  3434612.2500,  3444947.2500,  3474796.7500,
         3655056.2500,  3692100.2500,  3740408.7500,  3794827.2500,
         3811069.7500,  3828682.2500,  3835722.5000,  3864727.7500,
         3876085.2500,  3878832.5000,  3885635.2500,  3887108.7500,
         3887290.2500,  3893722.0000,  3903814.2500,  3940209.2500,
         3951505.0000,  3964481.7500,  3965860.5000,  3982860.0000,
         3984226

In [39]:
ipd.Audio(data=wav3.numpy(), autoplay=True, rate=sr)

In [40]:
## Посмотрим на представления wa2vec

In [41]:
batch.features[194]

tensor([[-3.5636, -3.5636, -3.5636,  ...,  1.4391,  0.7881,  0.7881],
        [-2.0741, -2.0741, -2.0741,  ...,  2.7419, -0.7855, -0.7855],
        [-3.2869, -3.2869, -3.2869,  ...,  3.3533,  3.3947,  3.3947],
        ...,
        [ 1.4543,  1.4543,  1.4543,  ..., -4.6328, -5.8794, -5.8794],
        [ 2.4781,  2.4781,  2.4781,  ...,  8.3305,  9.3026,  9.3026],
        [ 5.9909,  5.9909,  5.9909,  ...,  0.2817, -0.1452, -0.1452]])

In [42]:
np.where(batch.features[193].cpu().numpy()==-3.5636)

(array([], dtype=int64), array([], dtype=int64))

In [53]:
batch.features[193][0, 61:]

tensor([-3.5636, -3.5636,  2.9353,  2.9353,  1.8879,  1.8879,  1.8879,  0.7238,
         0.7238,  1.8979,  1.8979,  1.8979,  6.1730,  6.1730,  1.7827,  1.7827,
        -1.8822, -1.8822, -1.8822, -9.1845, -9.1845,  4.1336,  4.1336,  4.1336,
         4.4724,  4.4724,  3.1925,  3.1925,  2.2269,  2.2269,  2.2269,  2.2938,
         2.2938,  1.4275,  1.4275,  1.4275,  2.8433,  2.8433,  3.0037,  3.0037,
         3.0037,  2.4795,  2.4795,  3.5388,  3.5388,  3.2663,  3.2663,  3.2663,
         3.6400,  3.6400,  6.7765,  6.7765,  6.7765,  4.0591,  4.0591,  0.8456,
         0.8456,  1.5608,  1.5608,  1.5608,  2.9129,  2.9129,  3.4115,  3.4115,
         3.4115,  4.3258,  4.3258,  7.4450,  7.4450,  7.5022,  7.5022,  7.5022,
         4.9845,  4.9845,  6.7074,  6.7074,  6.7074,  6.0065,  6.0065,  7.9259,
         7.9259,  1.4767,  1.4767,  1.4767,  3.2169,  3.2169,  5.7036,  5.7036,
         5.7036,  5.2859,  5.2859,  1.9061,  1.9061,  2.3567,  2.3567,  2.3567,
        -2.8596, -2.8596, -2.7638, -2.76

In [44]:
batch.features[194][0, :]

tensor([-3.5636, -3.5636, -3.5636,  2.9353,  2.9353,  1.8879,  1.8879,  1.8879,
         0.7238,  0.7238,  1.8979,  1.8979,  1.8979,  6.1730,  6.1730,  1.7827,
         1.7827, -1.8822, -1.8822, -1.8822, -9.1845, -9.1845,  4.1336,  4.1336,
         4.1336,  4.4724,  4.4724,  3.1925,  3.1925,  2.2269,  2.2269,  2.2269,
         2.2938,  2.2938,  1.4275,  1.4275,  1.4275,  2.8433,  2.8433,  3.0037,
         3.0037,  2.4795,  2.4795,  2.4795,  3.5388,  3.5388,  3.2663,  3.2663,
         3.2663,  3.6400,  3.6400,  6.7765,  6.7765,  4.0591,  4.0591,  4.0591,
         0.8456,  0.8456,  1.5608,  1.5608,  1.5608,  2.9129,  2.9129,  3.4115,
         3.4115,  4.3258,  4.3258,  4.3258,  7.4450,  7.4450,  7.5022,  7.5022,
         7.5022,  4.9845,  4.9845,  6.7074,  6.7074,  6.0065,  6.0065,  6.0065,
         7.9259,  7.9259,  1.4767,  1.4767,  1.4767,  3.2169,  3.2169,  5.7036,
         5.7036,  5.2859,  5.2859,  5.2859,  1.9061,  1.9061,  2.3567,  2.3567,
         2.3567, -2.8596, -2.8596, -2.76

In [45]:
batch.features[195][0, :]

tensor([ 2.9129,  2.9129,  2.9129,  3.4115,  3.4115,  4.3258,  4.3258,  4.3258,
         7.4450,  7.4450,  7.5022,  7.5022,  7.5022,  4.9845,  4.9845,  6.7074,
         6.7074,  6.0065,  6.0065,  6.0065,  7.9259,  7.9259,  1.4767,  1.4767,
         1.4767,  3.2169,  3.2169,  5.7036,  5.7036,  5.2859,  5.2859,  5.2859,
         1.9061,  1.9061,  2.3567,  2.3567,  2.3567, -2.8596, -2.8596, -2.7638,
        -2.7638,  2.1738,  2.1738,  2.1738,  1.7959,  1.7959,  4.4534,  4.4534,
         4.4534,  2.7165,  2.7165,  4.7661,  4.7661, -1.4313, -1.4313, -1.4313,
         3.1147,  3.1147,  1.5131,  1.5131,  1.5131,  3.7576,  3.7576,  3.1129,
         3.1129,  2.5082,  2.5082,  2.5082,  3.3445,  3.3445,  4.6618,  4.6618,
         4.6618,  5.0756,  5.0756, -5.0255, -5.0255,  2.9494,  2.9494,  2.9494,
         3.2018,  3.2018,  5.1544,  5.1544,  5.1544,  4.1407,  4.1407,  5.8795,
         5.8795,  3.0667,  3.0667,  3.0667, -2.3209, -2.3209,  0.0972,  0.0972,
         0.0972, -1.4725, -1.4725,  1.35

In [46]:
output[0][0,62:]

tensor([-0.2926, -1.0800, -1.0800, -0.9219, -0.9219, -0.9219, -1.1583, -1.1583,
        -1.0925, -1.0925, -1.0925, -0.8758, -0.8758, -0.3594, -0.3594,  0.0035,
         0.0035,  0.0035, -0.4936, -0.4936, -0.1811, -0.1811, -0.1811,  0.5403,
         0.5403,  0.6332,  0.6332,  0.1428,  0.1428,  0.1428, -0.8076, -0.8076,
        -0.9398, -0.9398, -0.9398, -0.5672, -0.5672, -0.4737, -0.4737, -0.4737,
        -0.8845, -0.8845, -0.3921, -0.3921, -0.3011, -0.3011, -0.3011, -0.3878,
        -0.3878, -0.3930, -0.3930, -0.3930, -0.4262, -0.4262, -0.4088, -0.4088,
        -0.4231, -0.4231, -0.4231, -0.3698, -0.3698, -0.3597, -0.3597, -0.3597,
        -0.3654, -0.3654, -0.4218, -0.4218, -0.4761, -0.4761, -0.4761, -0.4610,
        -0.4610, -0.3738, -0.3738, -0.3738, -0.3383, -0.3383, -0.3170, -0.3170,
        -0.3216, -0.3216, -0.3216, -0.3342, -0.3342, -0.2704, -0.2704, -0.2704,
        -0.2324, -0.2324, -0.2161, -0.2161, -0.1887, -0.1887, -0.1887, -0.1499,
        -0.1499, -0.0989, -0.0989, -0.09

In [47]:
output[1][0,:-61]

tensor([-0.2926, -0.2926, -0.2926, -1.0800, -1.0800, -0.9219, -0.9219, -0.9219,
        -1.1583, -1.1583, -1.0925, -1.0925, -1.0925, -0.8758, -0.8758, -0.3594,
        -0.3594,  0.0035,  0.0035,  0.0035, -0.4936, -0.4936, -0.1811, -0.1811,
        -0.1811,  0.5403,  0.5403,  0.6332,  0.6332,  0.1428,  0.1428,  0.1428,
        -0.8076, -0.8076, -0.9398, -0.9398, -0.9398, -0.5672, -0.5672, -0.4737,
        -0.4737, -0.8845, -0.8845, -0.8845, -0.3921, -0.3921, -0.3011, -0.3011,
        -0.3011, -0.3878, -0.3878, -0.3930, -0.3930, -0.4262, -0.4262, -0.4262,
        -0.4088, -0.4088, -0.4231, -0.4231, -0.4231, -0.3698, -0.3698, -0.3597,
        -0.3597, -0.3654, -0.3654, -0.3654, -0.4218, -0.4218, -0.4761, -0.4761,
        -0.4761, -0.4610, -0.4610, -0.3738, -0.3738, -0.3383, -0.3383, -0.3383,
        -0.3170, -0.3170, -0.3216, -0.3216, -0.3216, -0.3342, -0.3342, -0.2704,
        -0.2704, -0.2324, -0.2324, -0.2324, -0.2161, -0.2161, -0.1887, -0.1887,
        -0.1887, -0.1499, -0.1499, -0.09

In [48]:
batch.features[0][0,62:]

tensor([-0.6895, -5.1445, -5.1445, -4.2501, -4.2501, -4.2501, -5.5878, -5.5878,
        -5.2154, -5.2154, -5.2154, -3.9895, -3.9895, -1.0675, -1.0675,  0.9861,
         0.9861,  0.9861, -1.8266, -1.8266, -0.0587, -0.0587, -0.0587,  4.0234,
         4.0234,  4.5491,  4.5491,  1.7740,  1.7740,  1.7740, -3.6034, -3.6034,
        -4.3515, -4.3515, -4.3515, -2.2431, -2.2431, -1.7138, -1.7138, -1.7138,
        -4.0384, -4.0384, -1.2524, -1.2524, -0.7374, -0.7374, -0.7374, -1.2278,
        -1.2278, -1.2577, -1.2577, -1.2577, -1.4452, -1.4452, -1.3471, -1.3471,
        -1.4277, -1.4277, -1.4277, -1.1262, -1.1262, -1.0689, -1.0689, -1.0689,
        -1.1015, -1.1015, -1.4204, -1.4204, -1.7274, -1.7274, -1.7274, -1.6420,
        -1.6420, -1.1487, -1.1487, -1.1487, -0.9478, -0.9478, -0.8276, -0.8276,
        -0.8537, -0.8537, -0.8537, -0.9247, -0.9247, -0.5635, -0.5635, -0.5635,
        -0.3485, -0.3485, -0.2563, -0.2563, -0.1014, -0.1014, -0.1014,  0.1181,
         0.1181,  0.4068,  0.4068,  0.40

In [49]:
batch.features[1][0,:-62]

tensor([-0.6895, -0.6895, -0.6895, -5.1445, -5.1445, -4.2501, -4.2501, -4.2501,
        -5.5878, -5.5878, -5.2154, -5.2154, -5.2154, -3.9895, -3.9895, -1.0675,
        -1.0675,  0.9861,  0.9861,  0.9861, -1.8266, -1.8266, -0.0587, -0.0587,
        -0.0587,  4.0234,  4.0234,  4.5491,  4.5491,  1.7740,  1.7740,  1.7740,
        -3.6034, -3.6034, -4.3515, -4.3515, -4.3515, -2.2431, -2.2431, -1.7138,
        -1.7138, -4.0384, -4.0384, -4.0384, -1.2524, -1.2524, -0.7374, -0.7374,
        -0.7374, -1.2278, -1.2278, -1.2577, -1.2577, -1.4452, -1.4452, -1.4452,
        -1.3471, -1.3471, -1.4277, -1.4277, -1.4277, -1.1262, -1.1262, -1.0689,
        -1.0689, -1.1015, -1.1015, -1.1015, -1.4204, -1.4204, -1.7274, -1.7274,
        -1.7274, -1.6420, -1.6420, -1.1487, -1.1487, -0.9478, -0.9478, -0.9478,
        -0.8276, -0.8276, -0.8537, -0.8537, -0.8537, -0.9247, -0.9247, -0.5635,
        -0.5635, -0.3485, -0.3485, -0.3485, -0.2563, -0.2563, -0.1014, -0.1014,
        -0.1014,  0.1181,  0.1181,  0.40

In [155]:
%%time
attn =conv1d(output[:,0,:].unsqueeze(1),output[:,0,:].unsqueeze(1),padding=output.shape[-1])
values, _ =torch.max(attn, axis=-1)
labels =torch.softmax(values, axis=-1)

CPU times: user 4.38 ms, sys: 146 µs, total: 4.53 ms
Wall time: 2.83 ms


In [158]:
F.cross_entropy(labels, labels)

tensor(4.6094, device='cuda:1')

In [96]:
batch._event_lists[0]

[DataSlice(start=96.25, duration=4.00833333333334, modality=None, language=None, sample_rate=120.0),
 Sound(start=94.165, duration=8.849999999999994, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', offset=85.92),
 Word(start=96.185, duration=0.1299999999999954, modality='audio', language='english', word='of', word_index=9, word_sequence='Chad checked the other fort out of the corner of his eye'),
 Word(start=96.315, duration=0.1400000000000005, modality='audio', language='english', word='his', word_index=10, word_sequence='Chad checked the other fort out of the corner of his eye'),
 Word(start=96.455, duration=0.0900000000000034, modality='audio', language='english', word='eye', word_index=11, word_sequence='Chad checked the other fort out of the corner of his eye'),
 Word(start=97.735, duration=0.2100000000000079, modality='audio', language='english', word='Two', word_index=0, word_s

In [97]:
batch._event_lists[1]

[DataSlice(start=96.75, duration=4.00833333333334, modality=None, language=None, sample_rate=120.0),
 Sound(start=94.165, duration=8.849999999999994, modality='audio', language='english', filepath='/home/zubrikhina/brainmagick_MICCAI/data/gwilliams2022/download/stimuli/audio/cable_spool_fort_0.wav', offset=85.92),
 Word(start=97.735, duration=0.2100000000000079, modality='audio', language='english', word='Two', word_index=0, word_sequence='Two forts stood on the playground and a hot bare battlefield separated them'),
 Word(start=97.945, duration=0.2999999999999971, modality='audio', language='english', word='forts', word_index=1, word_sequence='Two forts stood on the playground and a hot bare battlefield separated them'),
 Word(start=98.245, duration=0.25, modality='audio', language='english', word='stood', word_index=2, word_sequence='Two forts stood on the playground and a hot bare battlefield separated them'),
 Word(start=98.495, duration=0.1200000000000045, modality='audio', langua